In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import math
from scipy.interpolate import interp1d
import matplotlib
from matplotlib.backends.backend_pdf import PdfPages
matplotlib.rcParams['pdf.fonttype'] = 42
matplotlib.rcParams['ps.fonttype'] = 42

from utils import set_to_nan_based_on_likelihood, plot_ebc,filter_and_interpolate

def ebc_bins(dlc_df, bin_size_angle=6,bin_size_distance=80): 
    top_left_corner = (dlc_df.iloc[0]['top_left_corner x'], dlc_df.iloc[0]['top_left_corner y'])
    top_right_corner = (dlc_df.iloc[0]['top_right_corner x'],dlc_df.iloc[0]['top_right_corner y'])
    bottom_left_corner = (dlc_df.iloc[0]['bottom_left_corner x'], dlc_df.iloc[0]['bottom_left_corner y'])
    bottom_right_corner = (dlc_df.iloc[0]['bottom_right_corner x'], dlc_df.iloc[0]['bottom_right_corner y'])
    angle_bins = np.arange(0,360,bin_size_angle)

    diagonal_distance_arena = math.hypot(top_right_corner[0] - bottom_left_corner[0], top_right_corner[1] - bottom_left_corner[1])
    distance_bins = np.arange(0,diagonal_distance_arena,bin_size_distance)
    return distance_bins,angle_bins

def rotate(origin, point, angle):
    """
    Rotate a point counterclockwise by a given angle around a given origin.

    The angle should be given in radians.
    """
    ox, oy = origin
    px, py = point

    qx = ox + math.cos(angle) * (px - ox) - math.sin(angle) * (py - oy)
    qy = oy + math.sin(angle) * (px - ox) + math.cos(angle) * (py - oy)
    return qx, qy

def lineLineIntersection(A, B, C, D):
    # Line AB represented as a1x + b1y = c1
    a1 = B[1] - A[1]
    b1 = A[0] - B[0]
    c1 = a1*(A[0]) + b1*(A[1])
 
    # Line CD represented as a2x + b2y = c2
    a2 = D[1] - C[1]
    b2 = C[0] - D[0]
    c2 = a2*(C[0]) + b2*(C[1])
 
    determinant = a1*b2 - a2*b1
 
    if (determinant == 0):
        # The lines are parallel. This is simplified
        # by returning a pair of FLT_MAX
        return 'parallel'
    else:
        x = (b2*c1 - b1*c2)/determinant
        y = (a1*c2 - a2*c1)/determinant
        return (x, y)


def calaculate_ebc_head(dlc_df,left_drive_x,left_drive_y,right_drive_x,right_dirve_y,ebc_angle_bin_size,ebc_dist_bin_size):
    top_left_corner = (dlc_df.iloc[0]['top_left_corner x'], dlc_df.iloc[0]['top_left_corner y'])
    top_right_corner = (dlc_df.iloc[0]['top_right_corner x'],dlc_df.iloc[0]['top_right_corner y'])
    bottom_left_corner = (dlc_df.iloc[0]['bottom_left_corner x'], dlc_df.iloc[0]['bottom_left_corner y'])
    bottom_right_corner = (dlc_df.iloc[0]['bottom_right_corner x'], dlc_df.iloc[0]['bottom_right_corner y'])
    distance_bins,angle_bins = ebc_bins(dlc_df,ebc_angle_bin_size,ebc_dist_bin_size)
    ebc_data_final = []
    for i in range(len(left_drive_x)):
        print(i, len(left_drive_x), "egocentric head") #TO VIEW PROGRESS
        ebc_bins_total = np.zeros((len(distance_bins),len(angle_bins)))
        for angle in range(0,360,3):
            center_neck_pos = (left_drive_x[i],left_drive_y[i])
            center_haunch_pos = (right_drive_x[i],right_dirve_y[i]) 
            center_neck_pos = rotate(center_haunch_pos,center_neck_pos,angle=math.radians(-1*angle))
            body_angle_radian_frame = math.atan2(center_haunch_pos[1]-center_neck_pos[1],center_haunch_pos[0]-center_neck_pos[0])

            body_angle_deg_frame = math.degrees(body_angle_radian_frame)

            if body_angle_deg_frame<0:
                body_angle_deg_frame = 360+body_angle_deg_frame
            

            if(body_angle_deg_frame==0):
                #left wall
                interpoint = lineLineIntersection(center_haunch_pos,center_neck_pos,bottom_left_corner,top_left_corner)
                min_distance = math.hypot(interpoint[0]-center_neck_pos[0],interpoint[1]-center_neck_pos[1])
                distance_bin_index = np.digitize(min_distance,distance_bins)
                angle_bin_index = np.digitize(angle,angle_bins)
                ebc_bins_total[distance_bin_index-1][angle_bin_index]+=1

            elif(body_angle_deg_frame>0 and body_angle_deg_frame<90):
                #left wall and top wall
                interpoint_l = lineLineIntersection(center_haunch_pos,center_neck_pos,bottom_left_corner,top_left_corner)
                interpoint_t = lineLineIntersection(center_haunch_pos,center_neck_pos,top_left_corner,top_right_corner)
                distance_from_point_l = math.hypot(interpoint_l[0]-center_neck_pos[0],interpoint_l[1]-center_neck_pos[1])
                distance_from_point_t = math.hypot(interpoint_t[0]-center_neck_pos[0],interpoint_t[1]-center_neck_pos[1])
                min_distance = min(distance_from_point_l,distance_from_point_t)
                distance_bin_index = np.digitize(min_distance,distance_bins)
                angle_bin_index = np.digitize(angle,angle_bins)
                ebc_bins_total[distance_bin_index-1][angle_bin_index-1]+=1
            
            elif(body_angle_deg_frame==90):
                #top wall
                interpoint = lineLineIntersection(center_haunch_pos,center_neck_pos,top_left_corner,top_right_corner)
                min_distance = math.hypot(interpoint[0]-center_neck_pos[0],interpoint[1]-center_neck_pos[1])
                distance_bin_index = np.digitize(min_distance,distance_bins)
                angle_bin_index = np.digitize(angle,angle_bins)
                ebc_bins_total[distance_bin_index-1][angle_bin_index-1]+=1

            elif(body_angle_deg_frame>90 and body_angle_deg_frame<180):
                #top wall and right wall
                interpoint_l = lineLineIntersection(center_haunch_pos,center_neck_pos,bottom_right_corner,top_right_corner)
                interpoint_t = lineLineIntersection(center_haunch_pos,center_neck_pos,top_left_corner,top_right_corner)
                distance_from_point_l = math.hypot(interpoint_l[0]-center_neck_pos[0],interpoint_l[1]-center_neck_pos[1])
                distance_from_point_t = math.hypot(interpoint_t[0]-center_neck_pos[0],interpoint_t[1]-center_neck_pos[1])
                min_distance = min(distance_from_point_l,distance_from_point_t)
                distance_bin_index = np.digitize(min_distance,distance_bins)
                angle_bin_index = np.digitize(angle,angle_bins)
                ebc_bins_total[distance_bin_index-1][angle_bin_index-1]+=1
                
            elif(body_angle_deg_frame==180):
                #right wall
                interpoint = lineLineIntersection(center_haunch_pos,center_neck_pos,bottom_right_corner,top_right_corner)
                min_distance = math.hypot(interpoint[0]-center_neck_pos[0],interpoint[1]-center_neck_pos[1])
                distance_bin_index = np.digitize(min_distance,distance_bins)
                angle_bin_index = np.digitize(angle,angle_bins) 
                ebc_bins_total[distance_bin_index-1][angle_bin_index-1]+=1

            elif(body_angle_deg_frame>180 and body_angle_deg_frame<270):
                #right wall and bottom wall
                
                interpoint_l = lineLineIntersection(center_haunch_pos,center_neck_pos,bottom_right_corner,top_right_corner)
                interpoint_t = lineLineIntersection(center_haunch_pos,center_neck_pos,bottom_left_corner,bottom_right_corner)
                distance_from_point_l = math.hypot(interpoint_l[0]-center_neck_pos[0],interpoint_l[1]-center_neck_pos[1])
                distance_from_point_t = math.hypot(interpoint_t[0]-center_neck_pos[0],interpoint_t[1]-center_neck_pos[1])
                min_distance = min(distance_from_point_l,distance_from_point_t)
                distance_bin_index = np.digitize(min_distance,distance_bins)
                angle_bin_index = np.digitize(angle,angle_bins)
                ebc_bins_total[distance_bin_index-1][angle_bin_index-1]+=1
            
            elif(body_angle_deg_frame == 270):
                #bottom wall
                interpoint = lineLineIntersection(center_haunch_pos,center_neck_pos,bottom_right_corner,bottom_left_corner)
                min_distance = math.hypot(interpoint[0]-center_neck_pos[0],interpoint[1]-center_neck_pos[1])
                distance_bin_index = np.digitize(min_distance,distance_bins)
                angle_bin_index = np.digitize(angle,angle_bins)
                ebc_bins_total[distance_bin_index-1][angle_bin_index-1]+=1
            
            else:
                #bottom wall and left wall
                interpoint_l = lineLineIntersection(center_haunch_pos,center_neck_pos,bottom_left_corner,top_left_corner)
                interpoint_t = lineLineIntersection(center_haunch_pos,center_neck_pos,bottom_left_corner,bottom_right_corner)
                distance_from_point_l = math.hypot(interpoint_l[0]-center_neck_pos[0],interpoint_l[1]-center_neck_pos[1])
                distance_from_point_t = math.hypot(interpoint_t[0]-center_neck_pos[0],interpoint_t[1]-center_neck_pos[1])
                min_distance = min(distance_from_point_l,distance_from_point_t)
                distance_bin_index = np.digitize(min_distance,distance_bins)
                if min_distance<=800:
                    angle_bin_index = np.digitize(angle,angle_bins)
                    #print(i,min_distance,distance_bin_index,angle_bin_index)
                    ebc_bins_total[distance_bin_index-1][angle_bin_index-1]+=1
        
        ebc_data_final.append(ebc_bins_total)
    return np.array(ebc_data_final)

In [1]:
import numpy as np
import pandas as pd

# Load the data
file = r'\\rhea\E\20240608\WT0008LN\FM\20240608_WT0008LN_M_FM_DMS1_angie_ephys_topDLCephys.h5'
dlc_df = pd.read_hdf(file, 'dlc_df')
phy_df = pd.read_hdf(file, 'phy_df')

# Parameters
fps = 59.99
likelihood_threshold = 0.95
model_dt = 1/fps # Frame duration in seconds
bin_width = 20 # Bin width angles
speed_threshold = 0.25
ebc_angle_bin_size = 3
ebc_dist_bin_size = 40

columns_of_interest = ['left_drive', 'right_drive', 'time']

# Adding timestamps to dlc file and only considering columns of interest
dlc_df['time'] = np.arange(len(dlc_df)) / fps

# Split dlc_df into two halves
half_len = len(dlc_df) // 2
dlc_df_1 = dlc_df.iloc[:half_len].copy()
dlc_df_2 = dlc_df.iloc[half_len:].copy()

In [5]:


# Function to process each half
def process_half(dlc_df_half):
    # Filter and interpolate
    model_data_df, model_t = filter_and_interpolate(dlc_df_half, columns_of_interest, likelihood_threshold, model_dt, fps)
    
    # Filter based on speed threshold
    model_data_df = model_data_df[model_data_df['speed'] > speed_threshold]
    
    # Get coordinates for ebc calculation
    center_neck_x = list(model_data_df['left_drive x'])
    center_neck_y = list(model_data_df['left_drive y'])
    center_haunch_x = list(model_data_df['right_drive x'])
    center_haunch_y = list(model_data_df['right_drive y'])
    
    # Calculate ebc
    ebc_data = calaculate_ebc_head(dlc_df_half, center_neck_x, center_neck_y, center_haunch_x, center_haunch_y, ebc_angle_bin_size, ebc_dist_bin_size)
    distance_bins, angle_bins = ebc_bins(dlc_df_half, ebc_angle_bin_size, ebc_dist_bin_size)
    
    ebc_data_avg = np.sum(ebc_data, axis=0)
    rbins = distance_bins.copy()
    abins = np.linspace(0, 2*np.pi, 121)
    
    model_data_df['egocentric'] = list(ebc_data)
    
    return model_data_df

# Process each half
model_data_df_1 = process_half(dlc_df_1)
model_data_df_2 = process_half(dlc_df_2)

# Now model_data_df_1 and model_data_df_2 contain the processed data for each half of dlc_df


d:\Pipeline\STA_Pipeline\utils.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[df[col] < threshold, [f'{prefix} x', f'{prefix} y']] = np.nan
d:\Pipeline\STA_Pipeline\utils.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[df[col] < threshold, [f'{prefix} x', f'{prefix} y']] = np.nan


0 107735 egocentric head
1 107735 egocentric head
2 107735 egocentric head
3 107735 egocentric head
4 107735 egocentric head
5 107735 egocentric head
6 107735 egocentric head
7 107735 egocentric head
8 107735 egocentric head
9 107735 egocentric head
10 107735 egocentric head
11 107735 egocentric head
12 107735 egocentric head
13 107735 egocentric head
14 107735 egocentric head
15 107735 egocentric head
16 107735 egocentric head
17 107735 egocentric head
18 107735 egocentric head
19 107735 egocentric head
20 107735 egocentric head
21 107735 egocentric head
22 107735 egocentric head
23 107735 egocentric head
24 107735 egocentric head
25 107735 egocentric head
26 107735 egocentric head
27 107735 egocentric head
28 107735 egocentric head
29 107735 egocentric head
30 107735 egocentric head
31 107735 egocentric head
32 107735 egocentric head
33 107735 egocentric head
34 107735 egocentric head
35 107735 egocentric head
36 107735 egocentric head
37 107735 egocentric head
38 107735 egocentric h

d:\Pipeline\STA_Pipeline\utils.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[df[col] < threshold, [f'{prefix} x', f'{prefix} y']] = np.nan
d:\Pipeline\STA_Pipeline\utils.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[df[col] < threshold, [f'{prefix} x', f'{prefix} y']] = np.nan


0 107023 egocentric head
1 107023 egocentric head
2 107023 egocentric head
3 107023 egocentric head
4 107023 egocentric head
5 107023 egocentric head
6 107023 egocentric head
7 107023 egocentric head
8 107023 egocentric head
9 107023 egocentric head
10 107023 egocentric head
11 107023 egocentric head
12 107023 egocentric head
13 107023 egocentric head
14 107023 egocentric head
15 107023 egocentric head
16 107023 egocentric head
17 107023 egocentric head
18 107023 egocentric head
19 107023 egocentric head
20 107023 egocentric head
21 107023 egocentric head
22 107023 egocentric head
23 107023 egocentric head
24 107023 egocentric head
25 107023 egocentric head
26 107023 egocentric head
27 107023 egocentric head
28 107023 egocentric head
29 107023 egocentric head
30 107023 egocentric head
31 107023 egocentric head
32 107023 egocentric head
33 107023 egocentric head
34 107023 egocentric head
35 107023 egocentric head
36 107023 egocentric head
37 107023 egocentric head
38 107023 egocentric h

In [10]:
model_data_df_1

left_drive x  left_drive y  right_drive x  right_drive y      speed  \
0         892.184143    209.159698     897.464508     233.962379  15.753279   
1         894.016571    213.093163     898.283722     237.768501  15.753279   
2         895.753815    215.835129     899.219208     240.119286  15.307289   
3         898.904816    217.074173     901.042480     241.027908  15.688982   
4         902.066986    217.600723     904.214752     241.027908  17.551869   
...              ...           ...            ...            ...        ...   
108881    687.394409    834.956970     697.975952     859.705994   1.510757   
108882    687.695007    835.311066     698.175598     860.069427   1.455459   
108883    687.939911    835.675079     698.181488     860.476929   1.455459   
108884    687.994385    835.906555     698.181488     860.654388   1.455459   
108885    687.994385    836.099670     698.169708     860.921173   1.455459   

                                               egocentric  
0       [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
1       [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
2       [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
3       [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
4       [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
...                                                   ...  
108881  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
108882  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
108883  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
108884  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
108885  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  

[107735 rows x 6 columns]

In [19]:
cell_numbers = phy_df.index
distance_bins,angle_bins = ebc_bins(dlc_df,ebc_angle_bin_size,ebc_dist_bin_size)
rbins = distance_bins.copy()
abins = np.linspace(0,2*np.pi, (360//ebc_angle_bin_size))
def calc_mrls(model_data_df):
    ebc_plot_data = []
    n=120
    m=27
    MRLS = []
    MALS = []
    for i in cell_numbers:
        spike_times = phy_df.loc[i]['spikeT']

        #removing spike times after camera stopped
        spike_times = spike_times[spike_times<=max(model_t)]

        #binning spikes
        sp_count_ind = np.digitize(spike_times,bins = model_t)

        #-1 because np.digitze is 1-indexed
        sp_count_ind = [i-1 for i in sp_count_ind]

        sp_count_ind = [i for i in sp_count_ind if i in model_data_df.index]

        cell_spikes_egocentric = model_data_df['egocentric'].loc[sp_count_ind]  

        cell_spikes_avg = np.sum(cell_spikes_egocentric,axis = 0)

        ebc_data_avg = np.sum(np.array(model_data_df['egocentric']),axis=0)
        cell_spikes_avg = np.divide(cell_spikes_avg,ebc_data_avg)
        
        cell_spikes_avg[np.isnan(cell_spikes_avg)] = 0
        
        ebc_plot_data.append(cell_spikes_avg)

        firing_rates = cell_spikes_avg.copy().T
        theta = abins.copy()
        MR = (1 / (n * m)) * np.sum(firing_rates * np.exp(1j * theta[:, None]), axis=(0, 1))
        MRL = np.abs(MR)
        MRA = np.angle(MR)

        MRLS.append(MRL)
        MALS.append(MRA)
    return MRLS,MALS

In [20]:
abins.shape

(120,)

In [24]:
MRLS_1,MALS_1 = calc_mrls(model_data_df_1)
MRLS_2,MALS_2 = calc_mrls(model_data_df_2)

C:\Users\plab\AppData\Local\Temp\ipykernel_20092\3264644970.py:30: RuntimeWarning: invalid value encountered in divide
  cell_spikes_avg = np.divide(cell_spikes_avg,ebc_data_avg)
C:\Users\plab\AppData\Local\Temp\ipykernel_20092\3264644970.py:30: RuntimeWarning: invalid value encountered in divide
  cell_spikes_avg = np.divide(cell_spikes_avg,ebc_data_avg)
C:\Users\plab\AppData\Local\Temp\ipykernel_20092\3264644970.py:30: RuntimeWarning: invalid value encountered in divide
  cell_spikes_avg = np.divide(cell_spikes_avg,ebc_data_avg)
C:\Users\plab\AppData\Local\Temp\ipykernel_20092\3264644970.py:30: RuntimeWarning: invalid value encountered in divide
  cell_spikes_avg = np.divide(cell_spikes_avg,ebc_data_avg)
C:\Users\plab\AppData\Local\Temp\ipykernel_20092\3264644970.py:30: RuntimeWarning: invalid value encountered in divide
  cell_spikes_avg = np.divide(cell_spikes_avg,ebc_data_avg)
C:\Users\plab\AppData\Local\Temp\ipykernel_20092\3264644970.py:30: RuntimeWarning: invalid value encounte

In [25]:
for i in range(len(MRLS_1)):
    print(MRLS_1[i]-MALS_2[i])

-1.87065208597493
-0.1897680317019643
-1.9204798134589105
0.14649928523896483
3.009262568821205
0.07254478451662735
0.17244355714880383
2.4953551822866604
-2.4303443290663
-0.7366590146357767
-2.558250235578498
-0.6450958226632845
-2.8349397565529575
-0.15218897387038058
-1.269107489790603
1.7816037006075978
-1.472813049222436
0.20251511397348404
1.6930909933056857
-2.2505032236854636
-1.5988591191521062
1.2592156163902848
-0.3007676000369287
1.9892781187706705
1.6584350047094953
0.5721415199593185
0.5245123945880317
0.37174511766437857
-0.607438012760832
0.3802302775351094
1.7392271109596842
